In [23]:
# import necessary packages
import gym
import numpy as np

env = gym.make("CartPole-v1")

def relu(mat):
    return np.multiply(mat, (mat > 0))

def relu_derivative(mat):
    return (mat > 0) * 1


class NNLayer:
    def __init__(self, input_size, output_size, activation=None, lr=0.001):
        self.input_size = input_size
        self.output_size = output_size

        self.weights = np.random.uniform(low=-0.5, high=0.5, size=(input_size, output_size))  # initialize weights
        self.activation_function = activation

        self.lr = lr

    def forward(self, inputs, remember_for_backprop=True):
        input_with_bias = np.append(inputs, 1)
        unactivated = None
        unactivated = np.dot(input_with_bias, self.weights)
        output = unactivated
        if self.activation_function != None:
            output = self.activation_function(output)
        if remember_for_backprop:
            self.backward_store_in = input_with_bias
            self.backward_store_out = np.copy(unactivated)
        return output

    def update_weights(self, gradient, gamma, cumulated_reward, t):
        self.weights += self.lr * (gamma ** t) * cumulated_reward * gradient


    def backward(self, gradient_from_above, gamma, cumulated_return, t):
        adjusted_mul = gradient_from_above
        if self.activation_function == None:
            adjusted_mul = np.multiply(relu_derivative(self.backward_store_out), gradient_from_above)
        D_i = np.dot(np.transpose(np.reshape(self.backward_store_in, (1, len(self.backward_store_in)))),
                     np.reshape(adjusted_mul, (1, len(adjusted_mul))))
        delta_i = np.dot(adjusted_mul, np.transpose(self.weights))[:-1]
        self.update_weights(D_i, gamma, cumulated_return, t)
        return delta_i


class RLAgent:
    env = None
    def __init__(self, env, num_hidden_layers=2, hidden_size=24, gamma=0.95):
        self.env = env
        self.hidden_size = hidden_size
        self.input_size = env.observation_space.shape[0]
        self.output_size = env.action_space.n
        self.num_hidden_layers = num_hidden_layers
        self.gamma = gamma
        self.layers = [
            NNLayer(self.input_size + 1, self.hidden_size, activation=relu),
            NNLayer(self.hidden_size + 1, self.hidden_size, activation=relu),
            NNLayer(self.hidden_size + 1, self.output_size)
        ]

    def select_action(self, observation):
        values = self.forward(np.asmatrix(observation), False)
        action_prob = np.exp(values - np.max(values)) / np.sum(np.exp(values - np.max(values)))
        random = np.random.random()
        print('random:', random)
        print('action prob:', action_prob[0])
        if  random < action_prob[0]:
            return 0
        return 1

    def get_returns(self, rewards_list):
        returns = []
        G = 0
        for r in reversed(rewards_list):
            G = r + self.gamma * G
            returns.insert(0, G)
        return returns

    def forward(self, observation, remember_for_backprop=True):
        vals = np.copy(observation)
        index = 0
        for layer in self.layers:
            vals = layer.forward(vals, remember_for_backprop)
            index = index + 1
        return vals

    def backward(self, observation, action, cumulated_return, t):
        values = self.forward(np.asmatrix(observation), True)
        delta = np.zeros_like(values)
        delta[action] = 1 / values[action]

        for layer in reversed(self.layers):
            delta = layer.backward(delta, self.gamma, cumulated_return, t)




NUM_EPISODES = 10_000
MAX_TIMESTEPS = 1_000
GAMMA = 0.95
hidden_layer_size = 64
num_hidden_layers = 2

model = RLAgent(env, num_hidden_layers, hidden_layer_size, GAMMA)

for i_episode in range(NUM_EPISODES):
    rewards_list = []
    actions_list = []
    states_list = []
    observation, _ = env.reset()
    
    states_list.append(observation)
    
    for t in range(MAX_TIMESTEPS):
        action = model.select_action(observation)
        print(action)
        prev_obs = observation
        observation, reward, terminated, truncated, info = env.step(action)
        done = terminated or truncated
        rewards_list.append(reward)
        actions_list.append(action)
        states_list.append(observation)
        if done:
            #print('Episode {} ended with total reward of {}'.format(i_episode, t))
            break
        
    G_t = model.get_returns(rewards_list)
    for i in range(len(G_t)):
        prev_obs, observation, action, reward = states_list[i], states_list[i + 1], actions_list[i], G_t[i]
        model.backward(prev_obs, action, reward, i + 1)


observation = env.reset()
for t in range(MAX_TIMESTEPS):
    action = model.select_action(observation)
    prev_obs = observation
    observation, reward, done, info = env.step(action)
    if done:
        break

print("Done")


random: 0.01130711283272523
action prob: 0.15168612797503764
0
random: 0.8859568431775824
action prob: 0.1360436814827645
1
random: 0.012308870268087801
action prob: 0.1492368206910897
0
random: 0.9777168448655091
action prob: 0.13777151376185864
1
random: 0.9241482533093439
action prob: 0.1465839206555217
1
random: 0.7196666972402866
action prob: 0.17101488975664464
0
random: 0.4718892164610998
action prob: 0.14544676653224442
0
random: 0.3758221021520297
action prob: 0.1404045594870398
0
random: 0.8387446930920048
action prob: 0.13526321589155585
0
random: 0.3736454302961961
action prob: 0.11763928087245934
0
random: 0.8780829143518445
action prob: 0.11009578146621543
0
random: 0.28163845272138954
action prob: 0.09910746588345253
0
random: 0.07327225132947324
action prob: 0.09161296395517342
0
random: 0.704557995335697
action prob: 0.08554478761061249
0
random: 0.2335126359674382
action prob: 0.075335804514229
0
random: 0.19586270082797985
action prob: 0.06618336324775914
0
random: 0

random: 0.531330036220612
action prob: 5.533613761416837e-83
0
random: 0.7397211709437105
action prob: 2.1512906951283297e-90
0
random: 0.6122380820909994
action prob: 9.153713831900452e-33
0
random: 0.7362918922034248
action prob: 1.674755836880618e-39
0
random: 0.33667808107842045
action prob: 2.801797597900793e-46
0
random: 0.4227296826689805
action prob: 4.676555201183866e-53
0
random: 0.885016959881514
action prob: 6.235450564651088e-60
0
random: 0.6893633059046581
action prob: 7.336190743668634e-67
0
random: 0.06282629402376061
action prob: 6.895521342074033e-74
0
random: 0.9276510429840774
action prob: 4.759558021536279e-81
0
random: 0.9923118477751226
action prob: 2.2766187519863014e-88
0
random: 0.7103704493067438
action prob: 7.521381084921146e-96
0
random: 0.6880876514956303
action prob: 6.205281334145134e-34
0
random: 0.4911178478951457
action prob: 7.638906378194942e-41
0
random: 0.5618841338241574
action prob: 8.497969824578506e-48
0
random: 0.2119354052624819
action prob

random: 0.32267840326100006
action prob: 5.644815675984411e-82
0
random: 0.43337635153065013
action prob: 3.1333256370355994e-99
0
random: 0.4367727292665017
action prob: 1.2573412736072859e-116
0
random: 0.13683444331864325
action prob: 3.7426629722097196e-134
0
random: 0.5090412675516945
action prob: 7.179067286446469e-152
0
random: 0.11681980470635345
action prob: 7.734245451492846e-170
0
random: 0.5045731685644785
action prob: 4.341944593468028e-188
0
random: 0.08002281804596634
action prob: 1.0704520907529925e-206
0
random: 0.3820684471520154
action prob: 1.0349152294742846e-225
0
random: 0.9040236659659994
action prob: 3.660875413412071e-245
0
random: 0.49237848982749965
action prob: 1.1824718866164429e-77
0
random: 0.8686380871195636
action prob: 9.845368132462453e-95
0
random: 0.5246518776215207
action prob: 6.421517158897918e-112
0
random: 0.06553832053415454
action prob: 3.119683258678732e-129
0
random: 0.5933224617853026
action prob: 9.996194131603487e-147
0
random: 0.273871

random: 0.2446075951604889
action prob: 6.231419802825703e-212
0
random: 0.8867358975014081
action prob: 1.4159161345073958e-244
0
random: 0.18427635169370815
action prob: 1.4656151333981368e-277
0
random: 0.05674535579440931
action prob: 4.958550568427e-311
0
random: 0.531923186862891
action prob: 0.0
0
random: 0.7362064143167232
action prob: 0.0
0
random: 0.4464289657347127
action prob: 0.0
0
random: 0.09843823946801844
action prob: 0.0
0
random: 0.28324501296044713
action prob: 1.2865372957188166e-140
0
random: 0.709434636637556
action prob: 2.6038744591386587e-174
0
random: 0.1322796935157352
action prob: 2.9281456480580937e-208
0
random: 0.9566612947134071
action prob: 1.965086477472483e-242
0
random: 0.004563570261306715
action prob: 6.561173273233821e-277
0
random: 0.18848722706433352
action prob: 7.823295848124e-312
0
random: 0.18858731769206338
action prob: 0.0
0
random: 0.1813274948108068
action prob: 0.0
0
random: 0.4922520151918435
action prob: 0.0
0
random: 0.5828623596081

random: 0.5349213854500816
action prob: 1.6399733977252557e-218
0
random: 0.2353296084170059
action prob: 8.35213420660951e-271
0
random: 0.4245573762103283
action prob: 2e-323
0
random: 0.6465419513205827
action prob: 0.0
0
random: 0.1268039653923051
action prob: 0.0
0
random: 0.39118108515343253
action prob: 0.0
0
random: 0.6783014163919981
action prob: 0.0
0
random: 0.9174952257605804
action prob: 0.0
0
random: 0.6511630979382157
action prob: 1.734837684427384e-218
0
random: 0.41362629394621775
action prob: 5.879320066216291e-269
0
random: 0.8959565087348166
action prob: 9.3843e-320
0
random: 0.021345254248749557
action prob: 0.0
0
random: 0.35896555924476503
action prob: 0.0
0
random: 0.43418320099652685
action prob: 0.0
0
random: 0.31022617397768393
action prob: 0.0
0
random: 0.47233068322127936
action prob: 0.0
0
random: 0.3738121025786605
action prob: 0.0
0
random: 0.17372493147313817
action prob: 0.0
0
random: 0.6470269591931359
action prob: 2.0014627298331695e-224
0
random: 0.

...

random: 0.9100461601213514
action prob: 0.0
0
random: 0.24721197548935148
action prob: 0.0
0
random: 0.1812903693326655
action prob: 0.0
0
random: 0.7136052877129493
action prob: 0.0
0
random: 0.2880536691126895
action prob: 0.0
0
random: 0.9427061189942668
action prob: 0.0
0
random: 0.6607658674793566
action prob: 0.0
0
random: 0.468245077950597
action prob: 0.0
0
random: 0.9265997801865072
action prob: 0.0
0
random: 0.83541305978528
action prob: 0.0
0
random: 0.04763237116537544
action prob: 0.0
0
random: 0.7145029697770131
action prob: 0.0
0
random: 0.44899347946209467
action prob: 0.0
0
random: 0.2519852671424295
action prob: 0.0
0
random: 0.5435473461964481
action prob: 0.0
0
random: 0.15625101131583474
action prob: 0.0
0
random: 0.011330349069499035
action prob: 0.0
0
random: 0.13143711046422546
action prob: 0.0
0
random: 0.9686769032106758
action prob: 0.0
0
random: 0.5889188268466771
action prob: 0.0
0
random: 0.37246533482407573
action prob: 0.0
0
random: 0.6910693102176036
ac

random: 0.41854102332084264
action prob: 0.0
0
random: 0.008293887031247227
action prob: 0.0
0
random: 0.041985700749503474
action prob: 0.0
0
random: 0.30137500550600294
action prob: 0.0
0
random: 0.558806522938628
action prob: 0.0
0
random: 0.09668392966460226
action prob: 0.0
0
random: 0.50346320663793
action prob: 0.0
0
random: 0.4117734633264628
action prob: 0.0
0
random: 0.6184458725790278
action prob: 0.0
0
random: 0.8177888258786813
action prob: 0.0
0
random: 0.48559609662657366
action prob: 0.0
0
random: 0.1237544385089755
action prob: 0.0
0
random: 0.21641531945301484
action prob: 0.0
0
random: 0.06524277002330059
action prob: 0.0
0
random: 0.4902838252999845
action prob: 0.0
0
random: 0.18135152019167144
action prob: 0.0
0
random: 0.23395496555366224
action prob: 0.0
0
random: 0.32416459492115957
action prob: 0.0
0
random: 0.15881497969475633
action prob: 0.0
0
random: 0.7628440996947671
action prob: 0.0
0
random: 0.44564442706837715
action prob: 0.0
0
random: 0.871694485290

random: 0.8982886785779958
action prob: 0.0
0
random: 0.17859135556486494
action prob: 0.0
0
random: 0.13750230223547544
action prob: 0.0
0
random: 0.9402961435572871
action prob: 0.0
0
random: 0.5322250329159914
action prob: 0.0
0
random: 0.22531930802553435
action prob: 0.0
0
random: 0.867217464621827
action prob: 0.0
0
random: 0.933177854295398
action prob: 0.0
0
random: 0.6938736880455502
action prob: 0.0
0
random: 0.12342749655272411
action prob: 0.0
0
random: 0.1537657868625436
action prob: 0.0
0
random: 0.4969491567588983
action prob: 0.0
0
random: 0.2604630400805814
action prob: 0.0
0
random: 0.3788945496412539
action prob: 0.0
0
random: 0.8799661195096145
action prob: 0.0
0
random: 0.34346599564440106
action prob: 0.0
0
random: 0.28114371297625107
action prob: 0.0
0
random: 0.40577168883885373
action prob: 0.0
0
random: 0.2426161038546103
action prob: 0.0
0
random: 0.8705471288501598
action prob: 0.0
0
random: 0.9687401849864996
action prob: 0.0
0
random: 0.8841726617479178
ac

random: 0.9954396375380912
action prob: 0.0
0
random: 0.697802779948526
action prob: 0.0
0
random: 0.41508710405413274
action prob: 0.0
0
random: 0.8032059768328539
action prob: 0.0
0
random: 0.151200022914582
action prob: 0.0
0
random: 0.510054768095406
action prob: 0.0
0
random: 0.6786003150223954
action prob: 0.0
0
random: 0.542904114926113
action prob: 0.0
0
random: 0.33933925878996696
action prob: 0.0
0
random: 0.26303218815756957
action prob: 0.0
0
random: 0.3803292271902038
action prob: 0.0
0
random: 0.7239144145942982
action prob: 0.0
0
random: 0.17189009293141333
action prob: 0.0
0
random: 0.9923784305990512
action prob: 0.0
0
random: 0.6096702673445342
action prob: 0.0
0
random: 0.775208097434086
action prob: 0.0
0
random: 0.4614848368888994
action prob: 0.0
0
random: 0.8392526003454641
action prob: 0.0
0
random: 0.5870619675838873
action prob: 0.0
0
random: 0.9090743227969685
action prob: 0.0
0
random: 0.23528254397385895
action prob: 0.0
0
random: 0.3181244526134922
action 

ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (2,) + inhomogeneous part.